In [15]:
%matplotlib qt
import matplotlib.pyplot as plt
from matplotlib.animation import FFMpegWriter
import numpy as np

In [16]:
%store -r
print(Detroittimezone)
print(Hometimezone)
print(Schooltimezone)

-0500
+0800
-0800


In [17]:
plt.rcParams['figure.figsize'] = [20, 20]

# Set background
fig = plt.figure()
img = plt.imread("warp daytime.png")
ax0 = fig.add_subplot(111)
ax0.imshow(img, alpha = 0.9)
ax0.axis("off")

###############################
### plot concentric circles ###
###############################

ax = fig.add_subplot(polar=True)
# Set 0 to be north
ax.set_theta_zero_location('S')

# Move clockwise
ax.set_theta_direction(-1)

# Set 12 hours instead of the degrees
dtheta = 15
lines, labels = plt.thetagrids(
    (0,   15, 30,    45,  60,  75,  90, 105, 120, 135,  
     150,  165,  180, 195,  210,  225,  240,   255, 270,   285, 300,  315,  330,  345), labels=(
    '24', '1', '2', '3', '4', '5', '6', '7', '8', '9', 
        '10', '11', '12', '13', '14', '15', '16', '17', '18', '19', '20', '21', '22', '23'), fmt=None)

# Set 0 to be the outer ring
R = 12
ax.set_rlim(R, 0, 1)

# Add ticks for time zone names
ax.set_rticks(np.arange(1, R, 1))

# Rotate ticks around the origin
ax.set_rlabel_position(90)

# Set grids and title
ax.grid(True)  # Default is true
title = 'A Clock for All Time Zones'
ax.set_title(title, va='bottom')

# Hide "figure 1"
fig.canvas.header_visible = False

# Make clock face transparent
ax.set_facecolor("None")
###############################
plt.show()

In [18]:
# White for GMT+
# Black for GMT-

######################
### Timezone Rings ###
######################
theta = np.linspace(0, 2 * np.pi, 1300)

#Detroit
Detroittimezone = -4
ring1 = theta * 0 + abs(Detroittimezone)
detroit = ax.plot(theta, ring1, color='000000', linestyle='dashed', label='Detroit', linewidth=3)
#Home
Hometimezone = 8
ring2 = theta * 0 + abs(Hometimezone)
home = ax.plot(theta, ring2, color='#ffffff', linestyle='dotted', label='Shanghai', linewidth=3)
#School
Schooltimezone = -7
ring3 = theta * 0 + abs(Schooltimezone)
school = ax.plot(theta, ring3, color='000000', linestyle='dotted', label='Berkeley', linewidth=3)
######################

############################
### work & sleep for GMT ###
############################
work_start = 9
work_end = 17 # Need to use military time
theta_work = np.linspace((work_start)*np.pi/12, (work_end)*np.pi/12, 360)
ax.fill_between(theta_work, 0, R, color='lightblue', alpha=0.5)

sleep_start = 22
sleep_end = 8 # Need to use military time
theta_sleep = np.linspace((sleep_start)*np.pi/12, (sleep_end+24)*np.pi/12, 360)
ax.fill_between(theta_sleep, 0, R, color='red', alpha=0.2)
############################

#######################
### plot clock hand ###
#######################
theta = np.linspace(0, 2 * np.pi, 1300)
r = theta / (0.1668 / 2 * np.pi)
# Reverse the direction of spiral and offset over 1
r_neg = r[::-1]-1
# Static hands
#ln = ax.plot(theta, r, color = 'orange', label='GMT+', linewidth=3)
#ln_neg = ax.plot(theta, r_neg, color = 'blue', label='GMT-', linewidth=3)
#######################
plt.show()

In [19]:
# Find intercepts to show time for timezones
def find_roots(x,y):
    s = np.abs(np.diff(np.sign(y))).astype(bool)
    return x[:-1][s] + np.diff(x)[s]/(np.abs(y[1:][s]/y[:-1][s])+1)

# x is theta, k's are the clock hands for GMT+/-, y's are the timezone rings
def find_intercepts(x,k,y):
    z = find_roots(x,k-y)
    ax.plot(z, np.interp(z, x, k), marker="s", ls="", ms=10, color="r")
    
find_intercepts(theta,r_neg,ring1)
find_intercepts(theta,r,    ring2)
find_intercepts(theta,r_neg,ring3)

In [20]:
ln = ax.plot(theta, r, color = '#ffffff', label='GMT+', linewidth=3)
ln_neg = ax.plot(theta, r_neg, color = '#000000', label='GMT-', linewidth=3)
ax.legend()
plt.show()

In [21]:
metadata = dict(title='Final Project', artist='Hanji Xu',comment='please work')
writer = FFMpegWriter(fps=15, metadata=metadata)

#############################
### animate rotating hand ###
#############################
with writer.saving(fig, "Final.mp4", dpi=200):
    nf = 360
    for _ in range(nf):
        # Every time, delete previous 2 clock hands and 3 intecepts
        for _ in range(5):
            ax.lines.pop(-1)
        
        # Rotation by angle
        theta = theta + (np.pi/180)  # adding 1 is adding 1 radian
        
        # Plot hands
        ln = ax.plot(theta, r, color = '#ffffff', label='GMT+', linewidth=3)
        ln_neg = ax.plot(theta, r_neg, color = '#000000', label='GMT-', linewidth=3)
        
        # Plot intercepts
        find_intercepts(theta,r_neg,ring1)
        find_intercepts(theta,r,    ring2)
        find_intercepts(theta,r_neg,ring3)
        
        ax.legend()
        plt.show()
        plt.draw()
        plt.pause(0.01)
        writer.grab_frame()
#############################


In [8]:
"""#ax.lines.pop(0) # erasing first
###############################
### animate mistake version ###
###############################
with writer.saving(fig, "Final.mp4", dpi=200):
    nf = 100
    for it in range(nf):
        theta += theta + (np.pi/180)  #mistake   
        ln = ax.plot(theta, r)
        ln
        plt.show()
        plt.draw()
        plt.pause(0.05)
        writer.grab_frame()
        ax.lines.pop(0) #mistake
###############################"""

'#ax.lines.pop(0) # erasing first\n###############################\n### animate mistake version ###\n###############################\nwith writer.saving(fig, "Final.mp4", dpi=200):\n    nf = 100\n    for it in range(nf):\n        theta += theta + (np.pi/180)  #mistake   \n        ln = ax.plot(theta, r)\n        ln\n        plt.show()\n        plt.draw()\n        plt.pause(0.05)\n        writer.grab_frame()\n        ax.lines.pop(0) #mistake\n###############################'